In [1]:
from IPython.display import display, HTML
from pydrake.all import MultibodyPlant, SceneGraph, PlanarSceneGraphVisualizer, MultibodyPositionToGeometryPose, DiagramBuilder, Parser, TrajectorySource, Simulator
import matplotlib.pyplot as plt
from multicartpole import swing_up, get_urdf, add_traj_stabilizer_finite_horizon_LQR, simulate_diagram

n_pend = 3
N = 21
R = 0.1

x_lim = 1
l_max = 1


urdf_opt = get_urdf(n_pend, l_max=l_max, name="opt", color = "0 0 0.5", alpha=0.2)
urdf_sim = get_urdf(n_pend, l_max=l_max, name="sim", color = "0 0.7 0.")

In [2]:
builder = DiagramBuilder()
scene_graph = SceneGraph()
scene_graph.set_name("scene graph")
plant_opt = MultibodyPlant(time_step=0.0)
plant_opt.set_name("plant opt")
plant_sim = MultibodyPlant(time_step=0.0)
plant_sim.set_name("plant sim")
builder.AddSystem(scene_graph)

plant_sim.RegisterAsSourceForSceneGraph(scene_graph)
plant_opt.RegisterAsSourceForSceneGraph(scene_graph)

Parser(plant_opt).AddModelsFromString(urdf_opt, "urdf")
plant_opt.Finalize()
Parser(plant_sim).AddModelsFromString(urdf_sim, "urdf")
plant_sim.Finalize()
builder.AddSystem(plant_sim)

result, x_traj, u_traj = swing_up(plant_opt, N=N, R=R)
print(result.is_success())

source_x = builder.AddSystem(TrajectorySource(x_traj))
source_x.set_name("source x")
source_u = builder.AddSystem(TrajectorySource(u_traj))
source_u.set_name("source u")

pos_to_pose = builder.AddSystem(MultibodyPositionToGeometryPose(plant_opt, input_multibody_state=True))
pos_to_pose.set_name("position to pose")
builder.Connect(source_x.get_output_port(0), pos_to_pose.get_input_port())
builder.Connect(source_u.get_output_port(0), plant_sim.get_actuation_input_port())

builder.Connect(pos_to_pose.get_output_port(), scene_graph.get_source_pose_port(plant_opt.get_source_id()))
builder.Connect(plant_sim.get_output_port(0), scene_graph.get_source_pose_port(plant_sim.get_source_id()))

fig, ax = plt.subplots()

visualizer = builder.AddSystem(PlanarSceneGraphVisualizer(scene_graph, xlim=[-x_lim - l_max, x_lim + l_max], ylim=[-l_max, l_max+0.5], show=False, ax=ax))
builder.Connect(scene_graph.get_query_output_port(), visualizer.get_input_port(0))

visualizer.set_name("visualizer")

diagram = builder.Build()

visualizer.start_recording()
simulate_diagram(diagram, x0=x_traj.value(0), t_max=x_traj.end_time())
ani = visualizer.get_recording_as_animation()

display(HTML(ani.to_jshtml()))

True


In [3]:
builder = DiagramBuilder()
scene_graph = SceneGraph()
scene_graph.set_name("scene graph")

plant_opt = MultibodyPlant(time_step=0.0)
plant_opt.set_name("plant opt")
plant_sim = MultibodyPlant(time_step=0.0)
plant_sim.set_name("plant sim")

builder.AddSystem(scene_graph)
plant_sim.RegisterAsSourceForSceneGraph(scene_graph)
plant_opt.RegisterAsSourceForSceneGraph(scene_graph)

Parser(plant_opt).AddModelsFromString(urdf_opt, "urdf")
plant_opt.Finalize()

Parser(plant_sim).AddModelsFromString(urdf_sim, "urdf")
plant_sim.Finalize()
builder.AddSystem(plant_sim)

result, x_traj, u_traj = swing_up(plant_opt, N=N, R=R)
print(result.is_success())

source_x = builder.AddSystem(TrajectorySource(x_traj))
source_x.set_name("source x")

regulator = add_traj_stabilizer_finite_horizon_LQR(plant_sim, builder, x_traj, u_traj)

pos_to_pose = builder.AddSystem(MultibodyPositionToGeometryPose(plant_opt, input_multibody_state=True))
pos_to_pose.set_name("position to pose")

fig, ax = plt.subplots()
visualizer = builder.AddSystem(PlanarSceneGraphVisualizer(scene_graph, xlim=[-x_lim - l_max, x_lim + l_max], ylim=[-l_max, l_max+0.5], show=False, ax=ax))
visualizer.set_name("visualizer")

builder.Connect(source_x.get_output_port(0), pos_to_pose.get_input_port())
builder.Connect(pos_to_pose.get_output_port(), scene_graph.get_source_pose_port(plant_opt.get_source_id()))
builder.Connect(plant_sim.get_output_port(0), scene_graph.get_source_pose_port(plant_sim.get_source_id()))
builder.Connect(scene_graph.get_query_output_port(), visualizer.get_input_port(0))

diagram = builder.Build()
diagram.set_name("swing-up diagram")

visualizer.start_recording()
simulate_diagram(diagram, x0=x_traj.value(0), t_max=x_traj.end_time())

ani = visualizer.get_recording_as_animation()
display(HTML(ani.to_jshtml()))

True
